In [1]:
from __future__ import print_function
from __future__ import division
import os
import pickle
import json
import subprocess
from IPython.display import display
from IPython.display import Audio
from IPython.display import Image
import bisect
from collections import namedtuple
import numpy as np
import pandas as pd
from collections import Counter
import matplotlib.pyplot as plt
import seaborn as sns
import textwrap
import random
import math
import scipy as sp
import scipy.io.wavfile as wav
from tqdm import tqdm

from matplotlib.ticker import MultipleLocator, \
     FormatStrFormatter, AutoMinorLocator
%matplotlib inline

In [2]:
from nmt_run import *

In [3]:
SOX = "sox"
SPH2PIPE = "../installs/wav/sph2pipe_v2.5/sph2pipe"
FEACALC = "../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc"

STANDFEAT = "../installs/origZRTools/plebdisc/standfeat"

In [4]:
mboshi_path = "/afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/"

In [5]:
train_wavs_path = os.path.join(mboshi_path, "train_wav")
test_wavs_path = os.path.join(mboshi_path, "dev_wav")

In [6]:
train_dev_ids = [w.replace(".wav", "") for w in os.listdir(train_wavs_path)]

In [7]:
test_ids = [w.replace(".wav", "") for w in os.listdir(test_wavs_path)]

In [8]:
len(train_dev_ids), len(set(train_dev_ids))

(4616, 4616)

In [9]:
random.seed("haha")
np.random.seed(10)
dev_ids = list(set(np.random.choice(train_dev_ids, 200, replace=False)))

In [10]:
len(dev_ids), len(set(dev_ids))

(200, 200)

In [11]:
train_ids = list(set(train_dev_ids) - set(dev_ids))

In [12]:
len(train_ids), len(dev_ids), len(test_ids)

(4416, 200, 514)

In [13]:
def clean_out_str(out_str):
    out_str = out_str.replace("=", " ")
    out_str = out_str.replace(",", " ")
    out_str = out_str.replace(".", " ")
    out_str = out_str.replace(",", " ")
    out_str = out_str.replace("`", "")
    out_str = out_str.replace('"', '')
    out_str = out_str.replace('¿', '')
    out_str = out_str.replace("''", "")
    out_str = out_str.replace(":", "")
    out_str = out_str.replace("!", " ")
    out_str = out_str.replace("|", "")
    out_str = out_str.replace(";", " ")
    out_str = out_str.replace("‐", " ")
    out_str = out_str.replace("-", " ")
    

    # for BPE
    out_str = out_str.replace("@@ ", "")
    out_str = out_str.replace("@@", "")

    out_str = out_str.strip().lower()
    return out_str

In [14]:
def read_text(text_path):
    all_words = []
    all_chars = []
    utt2words = {}
    with open(text_path, "r", encoding="utf-8") as in_f:
        for line in in_f:
            u, t = line.split(" ", 1)
            t = clean_out_str(t)
            utt2words[u] = t
            curr_words = [w.strip() for w in t.split()]
            all_words.extend(curr_words)
            all_chars.extend([c for c in t])
        # end for line
    # end with
    fr_chars = Counter(all_chars)
#     fr_chars = {}
#     for w in all_words:
#         for c in w:
#             if c not in fr_chars:
#                 fr_chars[c] = 1
#             else:
#                 fr_chars[c] += 1
    return utt2words, Counter(all_words), fr_chars
    

In [15]:
mboshi_train_dev_text, mboshi_train_dev_words, mboshi_train_dev_chars = read_text(os.path.join(mboshi_path, 
                                                                                               "train.fr"))

In [16]:
sum(mboshi_train_dev_words.values()), len(mboshi_train_dev_words)

(36030, 5116)

In [17]:
sum(mboshi_train_dev_chars.values()), len(mboshi_train_dev_chars)

(189396, 45)

In [18]:
mboshi_test_text, mboshi_test_words, mboshi_test_chars = read_text(os.path.join(mboshi_path, "dev.fr"))

In [19]:
sum(mboshi_test_words.values()), len(mboshi_test_words)

(3954, 1200)

In [20]:
len(set(mboshi_train_dev_text.keys()) - set(train_ids))

200

In [21]:
def write_id_file(ids, out_fname):
    with open(out_fname, "w", encoding="utf-8") as out_f:
        for i in ids:
            out_f.write("{0:s}\n".format(i))
        # end for
    # end with        

In [22]:
def write_text_file(ids, text_dict, out_fname):
    with open(out_fname, "w", encoding="utf-8") as out_f:
        for i in ids:
            out_f.write("{0:s}\n".format(text_dict[i]))
        # end for
    # end with        

In [23]:
id_sets = {"mboshi_train": train_ids, "mboshi_dev": dev_ids, "mboshi_test": test_ids}
text_sets = {"mboshi_train": mboshi_train_dev_text, 
             "mboshi_dev": mboshi_train_dev_text, 
             "mboshi_test": mboshi_test_text}
set_paths = {k: os.path.join("./mboshi", "{0:s}.fr".format(k)) for k in id_sets}
set_id_paths = {k: os.path.join("./mboshi", "{0:s}.ids".format(k)) for k in id_sets}

In [24]:
set_paths, set_id_paths

({'mboshi_dev': './mboshi/mboshi_dev.fr',
  'mboshi_test': './mboshi/mboshi_test.fr',
  'mboshi_train': './mboshi/mboshi_train.fr'},
 {'mboshi_dev': './mboshi/mboshi_dev.ids',
  'mboshi_test': './mboshi/mboshi_test.ids',
  'mboshi_train': './mboshi/mboshi_train.ids'})

In [25]:
for i in id_sets:
    write_id_file(id_sets[i], set_id_paths[i])
    write_text_file(id_sets[i], text_sets[i], set_paths[i])

In [26]:
for c in mboshi_train_dev_chars:
    print(c, end=", ")

c, e,  , s, i, n, g, q, u, v, d, k, o, t, r, p, h, è, m, a, b, l, f, y, x, é, à, â, ', j, ê, ç, z, î, ô, ù, w, û, ë, á, ï, í, ì, 5, 0, 

In [27]:
def create_new_vocab(words):
    out = {"w2i":{}, "i2w":{}, "freq":{}}
    START_VOCAB = [PAD, GO, EOS, UNK]
    for w in START_VOCAB:
        out['w2i'][w] = len(out["w2i"])
        out["freq"][w] = 1
    #for w in words_list['words']:
    sorted_w = sorted(words.items(), reverse=True, key=lambda t: t[1])
    for w in sorted_w:
        encoded_word = w[0].encode()
        out["w2i"][encoded_word] = len(out["w2i"])
        out["freq"][encoded_word] = w[1]

    out["i2w"] = {val:key for key, val in out["w2i"].items()}
    return out

In [28]:
fr_vocab = {}

In [29]:
fr_vocab["en_c"] = create_new_vocab(mboshi_train_dev_chars)

In [30]:
fr_vocab["en_w"] = create_new_vocab(mboshi_train_dev_words)

In [31]:
fr_vocab.keys()

dict_keys(['en_c', 'en_w'])

In [32]:
fr_vocab["en_c"].keys()

dict_keys(['w2i', 'i2w', 'freq'])

In [33]:
pickle.dump(fr_vocab, open("./mfcc_13dim/mboshi_train_vocab.dict", "wb"))

In [34]:
eng_vocab = pickle.load(open("./mfcc_13dim/bpe_train_vocab.dict", "rb"))

In [35]:
eng_vocab.keys()

dict_keys(['es_w', 'es_c', 'en_w', 'en_c', 'bpe_w'])

In [36]:
eng_vocab["en_c"].keys()

dict_keys(['w2i', 'i2w', 'freq'])

In [37]:
en_chars = [c.decode() for c in eng_vocab["en_c"]["w2i"].keys()]

In [38]:
train_ids[:4]

['abiayi_2015-09-08-11-33-57_samsung-SM-T530_mdw_elicit_Dico18_191',
 'abiayi_2015-09-08-15-33-17_samsung-SM-T530_mdw_elicit_Dico15_9',
 'kouarata_2016-02-18-12-28-26_samsung-SM-T530_mdw_elicit_Part5_80',
 'abiayi_2015-09-09-09-37-54_samsung-SM-T530_mdw_elicit_Dico13_104']

In [39]:
def create_mboshi_map():
    oov = {}
    mboshi_map = {}
    
    for id_set in id_sets:
        print(id_set)
        mboshi_map[id_set] = {}
        oov[id_set] = []
        for i in id_sets[id_set]:
            mboshi_map[id_set][i] = {}            
            words = text_sets[id_set][i].split()
            encoded_words = [w.encode() for w in words]
            encoded_chars = [c.encode() for c in text_sets[id_set][i]]
            
            mboshi_map[id_set][i]["en_w"] = encoded_words
            mboshi_map[id_set][i]["en_c"] = encoded_chars
            
            for c in encoded_chars:
                if c not in fr_vocab["en_c"]["w2i"]:
                    oov[id_set].append(c)
    return mboshi_map, oov

In [40]:
mboshi_map, oov = create_mboshi_map()

mboshi_train
mboshi_dev
mboshi_test


In [41]:
pickle.dump(mboshi_map, open("./mfcc_13dim/mboshi_map.dict", "wb"))

In [42]:
oov

{'mboshi_dev': [], 'mboshi_test': [], 'mboshi_train': []}

In [43]:
wav_path = en_path = os.path.join(ainu_path, "wav")
en_path = os.path.join(ainu_path, "encl")

NameError: name 'ainu_path' is not defined

In [ ]:
ids = [w.replace(".wav", "") for w in os.listdir(wav_path)]

In [44]:
'0.000'.split(".",1)

['0', '000']

In [ ]:
utt2spk = {k: k.split(".",1)[0] for k in ids}
spk2utt = {}

for k in ids:
    spk_key = k.split(".",1)[0]
    if spk_key in spk2utt:
        spk2utt[spk_key].append(k)
    else:
        spk2utt[spk_key] = []
        
print("# of utts = {0:d}".format(len(ids)))
print("# of narratives = {0:d}".format(len(spk2utt)))
for s in spk2utt:
    print(s, len(spk2utt[s]))

In [ ]:
out_path = os.path.join(ainu_path, "text")

In [ ]:
ids_file = os.path.join(out_path, "ainu10.ids")
text_file = os.path.join(out_path, "ainu10.clean.en")
bpe_file = os.path.join(out_path, "ainu10.BPE_1000.en")

In [ ]:
with open(ids_file, "w", encoding="utf-8") as ids_f, open(text_file, "w", encoding="utf-8") as text_f:
    for i in ids:
        ids_f.write("{0:s}\n".format(i))
        with open(os.path.join(en_path, "{0:s}.en.cl".format(i)), "r") as en_f:
            lines = en_f.readlines()
            text = clean_out_str(lines[0].strip())
            if len(lines) > 1:
                print(i, len(lines))
            text_f.write("{0:s}\n".format(text))
    

### Create MFCCs, and normalize them

In [45]:
wav_path = '/afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/wavs'
mfcc_path = '/afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_raw'
mfcc_std_path = '/afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_std'
mfcc_final_path = '/afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mboshi_mfccs'

In [46]:
for id_set in id_sets:
    ids = id_sets[id_set]
    for i in tqdm(ids, ncols=80):
        wav_fname = os.path.join(wav_path, "{0:s}.wav".format(i))
        mfcc_fname = os.path.join(mfcc_path, "{0:s}.mfcc".format(i))
        mfcc_std_fname = os.path.join(mfcc_std_path, "{0:s}.std.mfcc".format(i))
        mfcc_final_fname = os.path.join(mfcc_final_path, "{0:s}".format(i))

        !$FEACALC -plp no -cep 13 -dom cep -deltaorder 0 -dither -frqaxis bark \
            -samplerate 16000 -win 25 -step 10 -ip MSWAVE -rasta false -compress true \
            -op swappedraw -o $mfcc_fname $wav_fname

        !$STANDFEAT -D 13 -infile $mfcc_fname -outfile $mfcc_std_fname

        out_mfcc = np.fromfile(mfcc_std_fname, dtype=np.float32)
        out_mfcc = out_mfcc.reshape((-1,13))
        print(out_mfcc.shape)
        np.save(mfcc_final_fname, out_mfcc)
        
    

  0%|                                                  | 0/4416 [00:00<?, ?it/s]

../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: Processing /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/wavs/abiayi_2015-09-08-11-33-57_samsung-SM-T530_mdw_elicit_Dico18_191.wav..
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: Finished (273 frames).
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: completed 1 utterance

Run Parameters
--------------
statsfile = (null), 
vadfile = (null), 
infile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_raw/abiayi_2015-09-08-11-33-57_samsung-SM-T530_mdw_elicit_Dico18_191.mfcc, 
outfile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_std/abiayi_2015-09-08-11-33-57_samsung-SM-T530_mdw_elicit_Dico18_191.std.mfcc, 
D = 13

infile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_raw/abiayi_2015-09-08-11-33-57_samsung-SM-T530_mdw_elicit_Dico18_191.mfcc; N = 

  0%|                                          | 1/4416 [00:00<55:59,  1.31it/s]

../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: Processing /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/wavs/abiayi_2015-09-08-15-33-17_samsung-SM-T530_mdw_elicit_Dico15_9.wav..
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: Finished (282 frames).
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: completed 1 utterance

Run Parameters
--------------
statsfile = (null), 
vadfile = (null), 
infile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_raw/abiayi_2015-09-08-15-33-17_samsung-SM-T530_mdw_elicit_Dico15_9.mfcc, 
outfile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_std/abiayi_2015-09-08-15-33-17_samsung-SM-T530_mdw_elicit_Dico15_9.std.mfcc, 
D = 13

infile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_raw/abiayi_2015-09-08-15-33-17_samsung-SM-T530_mdw_elicit_Dico15_9.mfcc; N = 282 fram

  0%|                                          | 2/4416 [00:01<39:11,  1.88it/s]

...

(263, 13)
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: Processing /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/wavs/martial_2015-09-07-15-24-49_samsung-SM-T530_mdw_elicit_Dico19_87.wav..
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: Finished (443 frames).
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: completed 1 utterance

Run Parameters
--------------
statsfile = (null), 
vadfile = (null), 
infile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_raw/martial_2015-09-07-15-24-49_samsung-SM-T530_mdw_elicit_Dico19_87.mfcc, 
outfile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_std/martial_2015-09-07-15-24-49_samsung-SM-T530_mdw_elicit_Dico19_87.std.mfcc, 
D = 13

infile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_raw/martial_2015-09-07-15-24-49_samsung-SM-T530_mdw_elicit_Dico19_87.

100%|████████████████████████████████████████▉| 513/514 [02:25<00:00,  3.52it/s]

(443, 13)
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: Processing /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/wavs/martial_2015-09-07-15-24-49_samsung-SM-T530_mdw_elicit_Dico19_89.wav..
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: Finished (413 frames).
../installs/wav/icsi-scenic-tools-20120105/feacalc-0.92/feacalc: completed 1 utterance

Run Parameters
--------------
statsfile = (null), 
vadfile = (null), 
infile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_raw/martial_2015-09-07-15-24-49_samsung-SM-T530_mdw_elicit_Dico19_89.mfcc, 
outfile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_std/martial_2015-09-07-15-24-49_samsung-SM-T530_mdw_elicit_Dico19_89.std.mfcc, 
D = 13

infile = /afs/inf.ed.ac.uk/group/project/ast/work/corpora/mboshi-french-parallel-corpus/mfcc_raw/martial_2015-09-07-15-24-49_samsung-SM-T530_mdw_elicit_Dico19_89.

100%|█████████████████████████████████████████| 514/514 [02:26<00:00,  3.52it/s]

(413, 13)


In [49]:
ha = np.load(os.path.join(mfcc_final_path, "abiayi_2015-09-08-11-18-39_samsung-SM-T530_mdw_elicit_Dico18_1.npy"))

In [50]:
ha.shape

(629, 13)

In [119]:
ha[:1]

array([[-0.91323674, -0.239832  , -0.05907755,  0.03795655,  0.10605837,
        -0.8245464 ,  1.2377436 , -0.49924138,  0.4513744 , -1.2282113 ,
        -1.5246838 ,  0.06962047,  0.7280074 ]], dtype=float32)

In [ ]:
haha = ha.reshape((-1,13))

In [ ]:
ha.shape, haha.shape

In [51]:
# for c in set(swbd1_ids) - {"swbd1_train_nodev"}:
info = {}
for c in id_sets:
    print(c)
    info[c] = {}
    for x in tqdm(id_sets[c], ncols=80):
        info[c][x] = {}
        t_data = np.load("./mfcc_13dim/mboshi_mfccs/{0:s}.npy".format(x))
        info[c][x]["sp"] = t_data.shape[0]
        info[c][x]["es_w"] = 0
        info[c][x]["es_c"] = 0
        info[c][x]["en_w"] = len(mboshi_map[c][x]["en_w"])
        info[c][x]["en_c"] = len(mboshi_map[c][x]["en_c"])

  1%|▎                                       | 40/4416 [00:00<00:11, 394.01it/s]

mboshi_train


 26%|██████████▊                              | 53/200 [00:00<00:00, 529.41it/s]

mboshi_dev


 10%|████▏                                    | 53/514 [00:00<00:00, 521.28it/s]

mboshi_test


100%|████████████████████████████████████████| 514/514 [00:00<00:00, 522.61it/s]


In [52]:
pickle.dump(info, open("./mfcc_13dim/info_mboshi.dict", "wb"))

In [53]:
durs = {}
for c in id_sets:
    print(c)
    durs[c] = []
    for x in tqdm(id_sets[c], ncols=80):
        t_data = np.load("./mfcc_13dim/mboshi_mfccs/{0:s}.npy".format(x))
        durs[c].append(t_data.shape[0])
        

  3%|█▎                                    | 149/4416 [00:00<00:02, 1489.26it/s]

mboshi_train


 54%|█████████████████████                  | 277/514 [00:00<00:00, 2767.53it/s]

mboshi_dev
mboshi_test


100%|███████████████████████████████████████| 514/514 [00:00<00:00, 2794.66it/s]


In [58]:
for c in durs:
    print(c)
    print("total hrs = {0:.3f}".format(sum(durs[c]) / 100. / 3600))
    print("min = {0:.2f}, max = {1:.2f}, mean = {2:.2f}".format(np.min(durs[c])/100, 
                                                                np.max(durs[c])/100, np.mean(durs[c])/100))

mboshi_train
total hrs = 3.824
min = 1.11, max = 9.74, mean = 3.12
mboshi_dev
total hrs = 0.173
min = 1.55, max = 6.70, mean = 3.12
mboshi_test
total hrs = 0.438
min = 1.39, max = 7.24, mean = 3.07


### Prepare seq-to-seq dictionaries

In [ ]:
cfg_path = "./mfcc_13dim/"
map_dict = pickle.load(open("../speech2text/mfcc_13dim/bpe_map.dict", "rb"))
vocab_dict = pickle.load(open("../speech2text/mfcc_13dim/bpe_train_vocab.dict", "rb"))

In [ ]:
map_dict.keys()

In [ ]:
spk2utt.keys()

In [ ]:
def create_ainu_map(train_spkrs, dev_spkrs, test_spkrs):
    oov = {}
    ainu_map = {}
    train_ids_str = "_".join(map(str, train_spkrs))
    dev_ids_str = "_".join(map(str, dev_spkrs))
    test_ids_str = "_".join(map(str, test_spkrs))
    
    ainu_map_fname = "ainu_train-{0:s}-dev-{1:s}-test-{2:s}_map.dict".format(train_ids_str, 
                                                                             dev_ids_str, 
                                                                             test_ids_str)
        
    
    with open(os.path.join("../subword-nmt/", "ainu10.BPE_1000.en"), "rb") as text_f, \
         open(os.path.join("../subword-nmt/", "ainu10.ids"), "r") as id_f, \
         open(os.path.join("../subword-nmt/", "ainu10.clean.en"), "rb") as words_f:
        for i, t, e in zip(id_f, text_f, words_f):
            curr_spkr = utt2spk[i.strip()]
            if curr_spkr in train_spkrs:
                c = "ainu_train-{0:s}".format(train_ids_str)
            elif curr_spkr in dev_spkrs:
                c = "ainu_dev-{0:s}".format(dev_ids_str)
            elif curr_spkr in test_spkrs:
                c = "ainu_test-{0:s}".format(test_ids_str)
            else:
                print(i, curr_spkr)
                print("Achtung!!")
            if c not in ainu_map:
                ainu_map[c] = {}
                oov[c] = []
            ainu_map[c][i.strip()] = {}
            ainu_map[c][i.strip()]["bpe_w"] = t.strip().split()
            ainu_map[c][i.strip()]["en_w"] = e.strip().split()
            ainu_map[c][i.strip()]["en_c"] = [tt.encode() for tt in e.strip().decode()]
            for w in t.strip().split():
                if w not in vocab_dict["bpe_w"]["w2i"]:
                    oov[c].append(w)
                    
            for w in t.strip().split():
                if w not in vocab_dict["bpe_w"]["w2i"]:
                    oov[c].append(w)

    print(ainu_map_fname)
    return ainu_map, ainu_map_fname, oov

In [ ]:
train_spkrs=[str(i) for i in range(2,10)]
dev_spkrs=['0']
test_spkrs=['1']

In [ ]:
ainu_map, ainu_map_fname, oov = create_ainu_map(train_spkrs=train_spkrs, 
                                                dev_spkrs=dev_spkrs, test_spkrs=test_spkrs)

In [ ]:
print([w.decode() for w in oov['ainu_train-2_3_4_5_6_7_8_9']])
print([w.decode() for w in oov['ainu_dev-0']])
print([w.decode() for w in oov['ainu_test-1']])

In [ ]:
ainu_map['ainu_train-2_3_4_5_6_7_8_9']['2.000']

In [ ]:
def create_ainu_ref(train_spkrs, dev_spkrs, test_spkrs):
    train_ids_str = "_".join(map(str, train_spkrs))
    dev_ids_str = "_".join(map(str, dev_spkrs))
    test_ids_str = "_".join(map(str, test_spkrs))
        
    ainu_ids = {}
    ainu_text = {}
    with open(os.path.join("../subword-nmt/", "ainu10.ids"), "r") as id_f, \
         open(os.path.join("../subword-nmt/", "ainu10.clean.en"), "r") as words_f:
        for i, e in zip(id_f, words_f):
            curr_spkr = utt2spk[i.strip()]
            if curr_spkr in train_spkrs:
                c = "ainu_train-{0:s}".format(train_ids_str)
            elif curr_spkr in dev_spkrs:
                c = "ainu_dev-{0:s}".format(dev_ids_str)
            elif curr_spkr in test_spkrs:
                c = "ainu_test-{0:s}".format(test_ids_str)
            else:
                print(i, curr_spkr)
                print("Achtung!!")
            if c not in ainu_ids:
                ainu_ids[c] = []
                ainu_text[c] = []
            
            ainu_ids[c].append(i.strip())
            ainu_text[c].append(e.strip())

    print(list(ainu_ids.keys()))
    return ainu_ids, ainu_text

In [ ]:
ainu_ids, ainu_text = create_ainu_ref(train_spkrs=train_spkrs, dev_spkrs=dev_spkrs, test_spkrs=test_spkrs)

In [ ]:
for c in ainu_text:
    with open("./mfcc_13dim/ainu/{0:s}.en".format(c), "w", encoding="utf-8") as out_f:
        for i in ainu_text[c]:
            out_f.write("{0:s}\n".format(i))
        # end for
    # end with
# end for

In [ ]:
print("writing ids to: {0:s}".format(ainu_map_fname.replace("map", "ids")))
pickle.dump(ainu_ids, open("./mfcc_13dim/ainu/{0:s}".format(ainu_map_fname.replace("map", "ids")), "wb"))

In [ ]:
print("writing map to: {0:s}".format(ainu_map_fname))
pickle.dump(ainu_map, open(os.path.join(cfg_path, ainu_map_fname), "wb"))
print("writing vocab to: {0:s}".format(ainu_map_fname.replace("_map", "_train_vocab")))
pickle.dump(vocab_dict, open(os.path.join(cfg_path, ainu_map_fname.replace("_map", "_train_vocab")), "wb"))

In [ ]:
info = pickle.load(open("../speech2text/mfcc_13dim/info.dict", "rb"))

In [ ]:
ainu_map.keys()

In [ ]:
# for c in set(swbd1_ids) - {"swbd1_train_nodev"}:
info = {}
for c in set(ainu_map.keys()):    
    info[c] = {}
    for x in tqdm(ainu_ids[c], ncols=80):
        info[c][x] = {}
        t_data = np.load("./mfcc_13dim/ainu_mfccs/{0:s}.npy".format(x))
        info[c][x]["sp"] = t_data.shape[0]
        info[c][x]["es_w"] = 0
        info[c][x]["es_c"] = 0
        info[c][x]["en_w"] = len(ainu_map[c][x]["en_w"])
        info[c][x]["en_c"] = len(" ".join([w.decode() for w in ainu_map[c][x]["en_w"]]))
    # end for        

In [ ]:
info.keys()

In [ ]:
print("writing info to: {0:s}".format("./mfcc_13dim/{0:s}".format(ainu_map_fname.replace("map", "info"))))
pickle.dump(info, open("./mfcc_13dim/{0:s}".format(ainu_map_fname.replace("map", "info")), "wb"))

In [ ]:
np.max(np.array([len(ainu_map["ainu_train-2_3_4_5_6_7_8_9"][x]["bpe_w"]) for x in info["ainu_train-2_3_4_5_6_7_8_9"]]))

In [ ]:
plt.hist(np.array([info["ainu_train-2_3_4_5_6_7_8_9"][x]["en_w"] for x in info["ainu_train-2_3_4_5_6_7_8_9"]]))

## Create MFCCs

In [ ]:
from python_speech_features import delta

In [ ]:
def create_mfb(wav_fname, mfb_fname, mfb_std_fname, nfilt=40):
    rate, sig = wav.read(wav_fname)
    mfb_feat = logfbank(sig,rate, nfilt=nfilt)
    d_mfb_feat = delta(mfb_feat, 2)
    dd_mfb_feat = delta(d_mfb_feat, 2)
    mfb_feat = np.concatenate((mfb_feat, d_mfb_feat), axis=1)
    mfb_feat = np.concatenate((mfb_feat, dd_mfb_feat), axis=1)
    try:
        mfb_feat_std = (mfb_feat - np.mean(mfb_feat, axis=0)) / np.std(mfb_feat, axis=0)
    except:
        print(wav_fname)
    # save mfb files
#     np.save(open(mfb_fname, "wb"), mfb_feat)
    np.save(open(mfb_std_fname, "wb"), mfb_feat_std.astype(np.float32))

In [ ]:
def create_mfcc(wav_fname, mfcc_fname, mfcc_std_fname):
    rate, sig = wav.read(wav_fname)
    mfcc_feat = mfcc(sig,rate)
    d_mfcc_feat = delta(mfcc_feat, 2)
    dd_mfcc_feat = delta(d_mfcc_feat, 2)
    mfcc_feat = np.concatenate((mfcc_feat, d_mfcc_feat), axis=1)
    mfcc_feat = np.concatenate((mfcc_feat, dd_mfcc_feat), axis=1)
    std_vals = np.std(mfcc_feat, axis=0)
    mfcc_feat_std = (mfcc_feat - np.mean(mfcc_feat, axis=0)) / np.std(mfcc_feat, axis=0)
    if not np.isfinite(std_vals).all() or not np.isfinite(std_vals).all():
        print("HAAAALP", wav_fname)
    # save mfcc files
#     np.save(open(mfcc_fname, "wb"), mfcc_feat)
    np.save(open(mfcc_std_fname, "wb"), mfcc_feat_std.astype(np.float32))

In [ ]:
def create_all_speech_features(mffc1mfb0=True):
    with tqdm(total=len(align_dict)) as pbar:
        for wav_fil in sorted(align_dict.keys()):
            for j, uttr in enumerate(sorted(align_dict[wav_fil].keys())):
                wav_fname = os.path.join(fa_vad_wavs_path, "{0:s}_fa_vad.wav".format(uttr))
                if mffc1mfb0:
                    mfcc_fname = os.path.join(fa_vad_mfcc_path, "{0:s}_fa_vad.mfcc".format(uttr))
                    mfcc_std_fname = os.path.join(fa_vad_std_mfcc_path, "{0:s}_fa_vad.std.mfcc".format(uttr))
                    create_mfcc(wav_fname, mfcc_fname, mfcc_std_fname)
                else:
                    mfb_fname = os.path.join(fa_vad_mfb_path, "{0:s}_fa_vad.mfb".format(uttr))
                    mfb_std_fname = os.path.join(fa_vad_std_mfb_path, "{0:s}_fa_vad.std.mfb".format(uttr))
                    create_mfb(wav_fname, mfb_fname, mfb_std_fname)
                
            # end for uttr
            pbar.update(1)
        # end for file
    # end pbar

    print("Completed!")

In [ ]:
create_all_speech_features(mffc1mfb0=False)

In [ ]:
for j, uttr in enumerate(sorted(align_dict['038'].keys())[20:]):
    print(uttr, end=', ')
    wav_fname = os.path.join(fa_vad_wavs_path, "{0:s}_fa_vad.wav".format(uttr))
    mfcc_fname = os.path.join(fa_vad_mfcc_path, "{0:s}_fa_vad.mfcc".format(uttr))
    mfcc_std_fname = os.path.join(fa_vad_std_mfcc_path, "{0:s}_fa_vad.std.mfcc".format(uttr))
    create_mfcc(wav_fname, mfcc_fname, mfcc_std_fname)
    

In [ ]:
!ls ../uttr_fa_vad_wavs/mfcc/ | wc

In [ ]:
haha = np.load("../uttr_fa_vad_wavs/mfcc/001.002_fa_vad.mfcc")

In [ ]:
haha_mfb = np.load("../uttr_fa_vad_wavs/mfb/001.002_fa_vad.mfb")

In [ ]:
haha.shape, haha_mfb.shape

In [ ]:
haha_mfb[0,:5]

In [ ]:
np.expand_dims(haha_mfb, 0)[0,0,-5:]

In [ ]:
np.flipud(haha_mfb)[-1,:5]

### etc code

In [ ]:
wavfile = os.path.join(uttr_wavs_path, "001.002.wav")
(rate,sig) = wav.read(wavfile)
mfcc_feat = mfcc(sig,rate)
mfb = logfbank(sig, rate, nfilt=80)

In [ ]:
mfb.shape, mfcc_feat.shape

In [ ]:
(rate,sig) = wav.read(wavfile)
mfcc_feat = mfcc(sig,rate)
d_mfcc_feat = delta(mfcc_feat, 2)
dd_mfcc_feat = delta(d_mfcc_feat, 2)
mfcc_feat = np.concatenate((mfcc_feat, d_mfcc_feat), axis=1)
mfcc_feat = np.concatenate((mfcc_feat, dd_mfcc_feat), axis=1)
mfcc_feat_std = (mfcc_feat - np.mean(mfcc_feat, axis=0)) / np.std(mfcc_feat, axis=0)
mfcc_feat.shape

In [ ]:
mfcc_feat.shape

In [ ]:
create_mfcc(wavfile, fa_vad_mfcc_path)

In [ ]:
!ls ../uttr_fa_vad_wavs/mfcc/

In [ ]:
os.path.basename(wavfile)

In [ ]:
mfcc_feat.shape, d_mfcc_feat.shape, dd_mfcc_feat.shape

In [ ]:
mfcc_feat_base[0,:], mfcc_feat[0, :13]

In [ ]:
d_mfcc_feat[0,:], mfcc_feat[0, 13:26]

In [ ]:
np.mean(mfcc_feat, axis=0).shape, np.std(mfcc_feat, axis=0).shape

In [ ]:
mfcc_feat_std = (mfcc_feat - np.mean(mfcc_feat, axis=0)) / np.std(mfcc_feat, axis=0)

In [ ]:
mfcc_feat_std[0, 13:26]

In [ ]:
Audio(os.path.join(uttr_wavs_path, "001.002.wav"))

In [ ]:
Audio(os.path.join(fa_vad_wavs_path, "001.002_fa_vad.wav"))

In [ ]:
print(" ".join([w.word for w in align_dict["110"]["110.005"]["es"]]))

In [ ]:
!soxi ../uttr_fa_vad_wavs/fa_vad_wavs/110.005_fa_vad.wav
!soxi ../uttr_fa_vad_wavs/uttr_wavs/110.005.wav

### Use MFCCs and Log Mel Filterbanks generated using Kaldi

In [ ]:
kaldi_out_path = "../uttr_fa_vad_wavs/kaldi/"

In [ ]:
haha = np.load("../uttr_fa_vad_wavs/mfcc_std/001.002_fa_vad.std.mfcc")

In [ ]:
haha.shape, haha[0,:5]

In [ ]:
!ls $kaldi_out_path/mfcc_cmvn_dd_vad

In [ ]:
kaldi_test = np.load("../uttr_fa_vad_wavs/kaldi/mfcc_cmvn_dd_vad/test.npz")

In [ ]:
kaldi_dev['001.002'].shape, kaldi_dev['001.002'][0,:5]